# N starvation 

## Which N sources allow HOT1A3 to grow

check out Escher visualization https://escher.readthedocs.io/en/latest/getting_started.html

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import cobra
import numpy as np
import seaborn as sns
import itertools
from matplotlib.colors import LogNorm, Normalize


In [2]:
import subprocess
import time


In [3]:
from cobra.flux_analysis import flux_variability_analysis
from cobra.flux_analysis import production_envelope


In [4]:
from cobra.flux_analysis import (
    single_gene_deletion, single_reaction_deletion, double_gene_deletion,
    double_reaction_deletion)

In [5]:
sns.hls_palette

<function seaborn.palettes.hls_palette(n_colors=6, h=0.01, l=0.6, s=0.65, as_cmap=False)>

In [6]:
def get_elements(rid):
    r = model.reactions.get_by_id(rid)
    m = r.reactants[0]    
    elements = m.elements.copy()
    
    res = {
        'reaction' : rid,
        'metabolite' : m.name,
        'mid' : m.id,
        'N' : 'N' in elements,
        'C' : 'C' in elements,
        
    }
    return pd.Series(res)

# Import model and manipulate based on Ofaim at el

In [7]:
import os
model_dpath = os.path.join('..', 'Models')
model_fname = 'HOT1A3_ncbi.xml'
model_fpath = os.path.join(model_dpath, model_fname)


In [8]:
model = cobra.io.read_sbml_model(model_fpath)

In [9]:
exchange_ids = [r.id for r in model.exchanges] # + ["R00024"]

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


In [10]:
print('reactions', len(model.reactions))
print('metabolites', len(model.metabolites))
print('genes', len(model.genes))

reactions 2341
metabolites 1546
genes 1025


In [11]:
model

<Model HOT1A3_ncbi at 0x247e8a71190>

In [12]:
cobra.Configuration()

solver: glpk
tolerance: 1e-07
lower_bound: -1000.0
upper_bound: 1000.0
processes: 5
cache_directory: C:\Users\Osnat\AppData\Local\opencobra\cobrapy\Cache
max_cache_size: 104857600
cache_expiration: None

In [13]:
exchange_ids

['EX_12ppd__R_e',
 'EX_12ppd__S_e',
 'EX_14glucan_e',
 'EX_15dap_e',
 'EX_25dkglcn_e',
 'EX_2ameph_e',
 'EX_2m35mdntha_e',
 'EX_35dnta_e',
 'EX_3h4atb_e',
 'EX_3mb_e',
 'EX_4hba_e',
 'EX_4hbald_e',
 'EX_4hbz_e',
 'EX_5dglcn_e',
 'EX_5drib_e',
 'EX_6atha_e',
 'EX_LalaLglu_e',
 'EX_abg4_e',
 'EX_abt_e',
 'EX_ac_e',
 'EX_acac_e',
 'EX_acald_e',
 'EX_acgam_e',
 'EX_actn__R_e',
 'EX_ade_e',
 'EX_adn_e',
 'EX_ala_L_asp__L_e',
 'EX_ala_L_glu__L_e',
 'EX_ala_L_thr__L_e',
 'EX_ala__D_e',
 'EX_ala__L_e',
 'EX_ala_gln_e',
 'EX_ala_his_e',
 'EX_ala_leu_e',
 'EX_alagly_e',
 'EX_alahis_e',
 'EX_alaleu_e',
 'EX_alathr_e',
 'EX_alatrp_e',
 'EX_alltn_e',
 'EX_arab__L_e',
 'EX_arbt6p_e',
 'EX_arbt_e',
 'EX_arg__L_e',
 'EX_asn__L_e',
 'EX_aso3_e',
 'EX_aso4_e',
 'EX_asp__L_e',
 'EX_bhb_e',
 'EX_btn_e',
 'EX_but_e',
 'EX_bz_e',
 'EX_ca2_e',
 'EX_cell4_e',
 'EX_cellb_e',
 'EX_cgly_e',
 'EX_chol_e',
 'EX_cinnm_e',
 'EX_cit_e',
 'EX_cl_e',
 'EX_co2_e',
 'EX_co_e',
 'EX_cobalt2_e',
 'EX_crn_e',
 'EX_csn_e',
 

In [14]:
model.reactions.get_by_id('EX_cyan_e')

<Reaction EX_cyan_e at 0x247fee86f10>

In [15]:
model.reactions.get_by_id('Growth')

<Reaction Growth at 0x247fef0d280>

# Identify N sources where MED4 grows on

In [16]:
len(model.medium)

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


238

In [17]:
len(exchange_ids)

238

In [18]:
# copied from MED4 model
pro99_mediums = ['Ammonia', 'Cadmium', 'Ca2+', 'Cl-', 'Cobalt ion', 'Copper',
       'Orthophosphate', 'H2O', 'HCO3-', 'H+', 'Fe2+', 'Photon',
       'Magnesium cation', 'Molybdenum', 'O2', 'K+', 'Selenate', 'Na+',
       'Strontium cation', 'Sulfate', 'Zn2+', 'Hydrogen peroxide']
print('\n'.join(pro99_mediums))

Ammonia
Cadmium
Ca2+
Cl-
Cobalt ion
Copper
Orthophosphate
H2O
HCO3-
H+
Fe2+
Photon
Magnesium cation
Molybdenum
O2
K+
Selenate
Na+
Strontium cation
Sulfate
Zn2+
Hydrogen peroxide


In [19]:
# what are the metabolites in the medium?
df_medium = pd.DataFrame({'mediumExchange' : model.medium.keys()})
df_medium = pd.DataFrame.from_records(df_medium.mediumExchange.apply(get_elements))


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


In [20]:
df_medium

reaction              metabolite         mid      N      C
0    EX_12ppd__R_e    (R)-Propane-1,2-diol  12ppd__R_e  False   True
1    EX_12ppd__S_e    (S)-Propane-1,2-diol  12ppd__S_e  False   True
2    EX_14glucan_e      1,4-alpha-D-glucan  14glucan_e  False   True
3       EX_15dap_e      1,5-Diaminopentane     15dap_e   True   True
4    EX_25dkglcn_e  2,5-diketo-D-gluconate  25dkglcn_e  False   True
..             ...                     ...         ...    ...    ...
233    EX_val__L_e                L-Valine    val__L_e   True   True
234       EX_xan_e                Xanthine       xan_e   True   True
235      EX_xtsn_e              Xanthosine      xtsn_e   True   True
236    EX_xyl__D_e                D-Xylose    xyl__D_e  False   True
237       EX_zn2_e                    Zinc       zn2_e  False  False

[238 rows x 5 columns]

In [21]:
pro99_df = pd.read_excel('HOT1A3_medium.xlsx')

In [22]:
pro99_df.head()

reaction              metabolite      N     C pro99 MED4 metabolite  \
0   EX_actn__R_e       R  Acetoin C4H8O2  False  True   NaN             NaN   
1       EX_bhb_e  (R)-3-Hydroxybutanoate  False  True   NaN             NaN   
2  EX_12ppd__R_e    (R)-Propane-1,2-diol  False  True   NaN             NaN   
3  EX_12ppd__S_e    (S)-Propane-1,2-diol  False  True   NaN             NaN   
4    EX_phedca_e  10 Phenyldecanoic acid  False  True   NaN             NaN   

  promm  
0   NaN  
1   NaN  
2   NaN  
3   NaN  
4   NaN

In [23]:
df_medium.loc[df_medium.metabolite.str.contains('ic')]

reaction                                 metabolite  \
8         EX_3h4atb_e        3 Hydroxy 4 acetylthiobutanoic acid   
9            EX_3mb_e                      3-Methylbutanoic acid   
15         EX_6atha_e                  6 acetylthiohexanoic acid   
84       EX_fe3dcit_e                           Fe(III)dicitrate   
85   EX_fe3pyovd_kt_e  Ferrypyoverdine  P putida KT2440 specific   
154         EX_lnlc_e          Linoleic acid (all cis C18:2) n-6   
182       EX_phedca_e                     10 Phenyldecanoic acid   
183       EX_phehpa_e                     7 Phenylheptanoic acid   
184       EX_phehxa_e                      6 Phenylhexanoic acid   
186      EX_phenona_e                      9 Phenylnonanoic acid   
187      EX_pheocta_e                      8 Phenyloctanoic acid   
188        EX_phept_e                       5 phenylvaleric acid   
198        EX_ptsla_e                         Petroselaidic acid   
199     EX_pyovd_kt_e              Pyoverdine  P putida specific   

               mid      N      C  
8         3h4atb_e  False  False  
9            3mb_e  False   True  
15         6atha_e  False   True  
84       fe3dcit_e  False   True  
85   fe3pyovd_kt_e   True   True  
154         lnlc_e  False   True  
182       phedca_e  False   True  
183       phehpa_e  False   True  
184       phehxa_e  False   True  
186      phenona_e  False   True  
187      pheocta_e  False   True  
188        phept_e  False   True  
198        ptsla_e  False   True  
199     pyovd_kt_e   True   True

In [24]:
pro99_df.loc[~pro99_df.reaction.isin(exchange_ids)]

reaction                        metabolite      N     C pro99  \
12      EX_4abut_e                  4-Aminobutanoate   True  True   NaN   
42       EX_btoh_e                           Butanol  False  True   NaN   
47       EX_chor_e                        Chorismate  False  True   NaN   
53     EX_alaala_e                D-Alanyl-D-alanine   True  True   NaN   
70       EX_glcn_e                       D-Gluconate  False  True   NaN   
82     EX_ser__D_e                          D-Serine   True  True   NaN   
125  EX_id3acald_e     Indole 3 acetaldehyde C10H9NO   True  True   NaN   
144     EX_metox_e    L Methionine S oxide C5H11NO3S   True  True   NaN   
160    EX_his__L_e                       L-Histidine   True  True   NaN   
168    EX_phe__L_e                   L-Phenylalanine   True  True   NaN   
172    EX_ser__L_e                          L-Serine   True  True   NaN   
173    EX_thr__L_e                       L-Threonine   True  True   NaN   
175    EX_trp__L_e                      L-Tryptophan   True  True   NaN   
176    EX_tyr__L_e                        L-Tyrosine   True  True   NaN   
180    EX_malthx_e                      Maltohexaose  False  True   NaN   
182      EX_malt_e                 Maltose C12H22O11  False  True   NaN   
192    EX_acmana_e            N-Acetyl-D-mannosamine   True  True   NaN   
193      EX_ncam_e                      Nicotinamide   True  True   NaN   
194       EX_nac_e                        Nicotinate   True  True   NaN   
202       EX_orn_e                         Ornithine   True  True   NaN   
206    EX_pacald_e                Phenylacetaldehyde  False  True   NaN   
218   EX_salchs2_e                    Salmochelin-S2   True  True   NaN   
226      EX_g3pe_e  Sn-Glycero-3-phosphoethanolamine   True  True   NaN   

    MED4 metabolite promm  
12              NaN   NaN  
42              NaN   NaN  
47              NaN   NaN  
53              NaN   NaN  
70              NaN   NaN  
82              NaN   NaN  
125             NaN   NaN  
144             NaN   NaN  
160             NaN   NaN  
168             NaN   NaN  
172             NaN   NaN  
173             NaN   NaN  
175             NaN   NaN  
176             NaN   NaN  
180             NaN   NaN  
182             NaN   NaN  
192             NaN   NaN  
193             NaN   yes  
194             NaN   yes  
202             NaN   NaN  
206             NaN   NaN  
218             NaN   NaN  
226             NaN   NaN

In [25]:
pro99_df.loc[~pro99_df.reaction.isin(exchange_ids), 'promm'] = np.NaN

In [26]:
promm_exchanges = pro99_df.loc[pro99_df.pro99.isin(['yes']) | pro99_df.promm.isin(['yes']), 'reaction']
pro99_exchanges = pro99_df.loc[pro99_df.pro99.isin(['yes']), 'reaction']
other_exchahges = [m for m in exchange_ids if m not in promm_exchanges]

In [27]:
#[m for m in exchange_ids if m not in pro99_df.reaction.values]
df_medium.loc[~df_medium.reaction.isin(pro99_df.reaction), ['reaction', 'metabolite']]

reaction                                         metabolite
2    EX_14glucan_e                                 1,4-alpha-D-glucan
3       EX_15dap_e                                 1,5-Diaminopentane
53      EX_cell4_e                    Cellulose (n=4 repeating units)
90        EX_fuc_e                                         L-fuculose
137    EX_hom__L_e                                       L-Homoserine
141       EX_ibt_e                                        Isobutyrate
167     EX_mnl1p_e                             D-Mannitol 1-phosphate
170    EX_mththf_e  (2R,4S)-2-methyl-2,3,3,4-tetrahydroxytetrahydr...
201      EX_quin_e                                            Quinate
205   EX_salchs4_e                                     Salmochelin-S4

In [28]:
#[m for m in exchange_ids if m not in pro99_df.reaction.values]
pro99_df.loc[~pro99_df.reaction.isin(df_medium.reaction), ['reaction', 'metabolite']]

reaction                        metabolite
12      EX_4abut_e                  4-Aminobutanoate
42       EX_btoh_e                           Butanol
47       EX_chor_e                        Chorismate
53     EX_alaala_e                D-Alanyl-D-alanine
70       EX_glcn_e                       D-Gluconate
82     EX_ser__D_e                          D-Serine
125  EX_id3acald_e     Indole 3 acetaldehyde C10H9NO
144     EX_metox_e    L Methionine S oxide C5H11NO3S
160    EX_his__L_e                       L-Histidine
168    EX_phe__L_e                   L-Phenylalanine
172    EX_ser__L_e                          L-Serine
173    EX_thr__L_e                       L-Threonine
175    EX_trp__L_e                      L-Tryptophan
176    EX_tyr__L_e                        L-Tyrosine
180    EX_malthx_e                      Maltohexaose
182      EX_malt_e                 Maltose C12H22O11
192    EX_acmana_e            N-Acetyl-D-mannosamine
193      EX_ncam_e                      Nicotinamide
194       EX_nac_e                        Nicotinate
202       EX_orn_e                         Ornithine
206    EX_pacald_e                Phenylacetaldehyde
218   EX_salchs2_e                    Salmochelin-S2
226      EX_g3pe_e  Sn-Glycero-3-phosphoethanolamine

In [29]:
pro99_df.head()

reaction              metabolite      N     C pro99 MED4 metabolite  \
0   EX_actn__R_e       R  Acetoin C4H8O2  False  True   NaN             NaN   
1       EX_bhb_e  (R)-3-Hydroxybutanoate  False  True   NaN             NaN   
2  EX_12ppd__R_e    (R)-Propane-1,2-diol  False  True   NaN             NaN   
3  EX_12ppd__S_e    (S)-Propane-1,2-diol  False  True   NaN             NaN   
4    EX_phedca_e  10 Phenyldecanoic acid  False  True   NaN             NaN   

  promm  
0   NaN  
1   NaN  
2   NaN  
3   NaN  
4   NaN

In [30]:
pro99_df.columns

Index(['reaction', 'metabolite', 'N', 'C', 'pro99', 'MED4 metabolite',
       'promm'],
      dtype='object')

In [31]:
df_medium.head()

reaction              metabolite         mid      N     C
0  EX_12ppd__R_e    (R)-Propane-1,2-diol  12ppd__R_e  False  True
1  EX_12ppd__S_e    (S)-Propane-1,2-diol  12ppd__S_e  False  True
2  EX_14glucan_e      1,4-alpha-D-glucan  14glucan_e  False  True
3     EX_15dap_e      1,5-Diaminopentane     15dap_e   True  True
4  EX_25dkglcn_e  2,5-diketo-D-gluconate  25dkglcn_e  False  True

In [32]:
pd.merge(df_medium, pro99_df[['reaction', 'metabolite', 'pro99', 'MED4 metabolite',
       'promm']], on='reaction', how='left', suffixes=['', '_luca']).to_excel('HOT1A3_medium_NCBI.xlsx')

In [33]:
# does it grow on promm?
with model:
    medium = model.medium
    for m in medium:
        medium[m] = 0.0
    for m in promm_exchanges:
        medium[m] = 1000.0
    model.medium = medium
    print ('model medium', model.medium)
    solution = model.optimize()
    print(model.summary())


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


model medium {'EX_ac_e': 1000.0, 'EX_btn_e': 1000.0, 'EX_ca2_e': 1000.0, 'EX_cl_e': 1000.0, 'EX_co2_e': 1000.0, 'EX_cobalt2_e': 1000.0, 'EX_cu2_e': 1000.0, 'EX_fe2_e': 1000.0, 'EX_glyc_e': 1000.0, 'EX_h2o2_e': 1000.0, 'EX_h2o_e': 1000.0, 'EX_h_e': 1000.0, 'EX_inost_e': 1000.0, 'EX_k_e': 1000.0, 'EX_lac__D_e': 1000.0, 'EX_lac__L_e': 1000.0, 'EX_mg2_e': 1000.0, 'EX_mn2_e': 1000.0, 'EX_mobd_e': 1000.0, 'EX_nh4_e': 1000.0, 'EX_o2_e': 1000.0, 'EX_pi_e': 1000.0, 'EX_pyr_e': 1000.0, 'EX_sel_e': 1000.0, 'EX_so4_e': 1000.0, 'EX_zn2_e': 1000.0}
Objective
1.0 Growth = 21.6120604568175

Uptake
------
Metabolite     Reaction     Flux  C-Number C-Flux
     ca2_e     EX_ca2_e   0.1125         0  0.00%
      cl_e      EX_cl_e   0.1125         0  0.00%
 cobalt2_e EX_cobalt2_e 0.002161         0  0.00%
     cu2_e     EX_cu2_e  0.01532         0  0.00%
     fe2_e     EX_fe2_e   0.3235         0  0.00%
    glyc_e    EX_glyc_e    764.8         3 61.97%
       h_e       EX_h_e    187.2         0  0.00%
    

In [34]:
# does it grow on pro99?
with model:
    medium = model.medium
    for m in medium:
        medium[m] = 0.0
    for m in pro99_exchanges:
        medium[m] = 1000.0
    model.medium = medium
    print ('model medium', model.medium)
    solution = model.optimize()
    print(model.summary())


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


model medium {'EX_ca2_e': 1000.0, 'EX_cl_e': 1000.0, 'EX_co2_e': 1000.0, 'EX_cobalt2_e': 1000.0, 'EX_cu2_e': 1000.0, 'EX_fe2_e': 1000.0, 'EX_h2o2_e': 1000.0, 'EX_h2o_e': 1000.0, 'EX_h_e': 1000.0, 'EX_k_e': 1000.0, 'EX_mg2_e': 1000.0, 'EX_mn2_e': 1000.0, 'EX_mobd_e': 1000.0, 'EX_nh4_e': 1000.0, 'EX_o2_e': 1000.0, 'EX_pi_e': 1000.0, 'EX_sel_e': 1000.0, 'EX_so4_e': 1000.0, 'EX_zn2_e': 1000.0}
Objective
1.0 Growth = 0.0

Uptake
------
Empty DataFrame
Columns: [Metabolite, Reaction, Flux, C-Number, C-Flux]
Index: []

Secretion
---------
Empty DataFrame
Columns: [Metabolite, Reaction, Flux, C-Number, C-Flux]
Index: []



In [35]:
# try to add each exchange one by one
results = list()

def _check_medium(met1, met2=None):
    with model:
        medium = model.medium
        for m in medium:
            medium[m] = 0.0
        for m in pro99_exchanges:
            medium[m] = 1000.0
        medium["EX_nh4_e"] = 0.0
        medium[met1] = 1000.0
        model.medium = medium
        solution = model.slim_optimize()
        return {'uptake' : met1, 'objective_value' : solution}
results = [_check_medium(met) for met in exchange_ids]        

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

...

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

In [36]:
df = pd.DataFrame(results)

In [37]:
df_growing = df.loc[(df.objective_value > 1e-5), 
                    ['uptake','objective_value']
                   ].nlargest(n=1000, columns='objective_value').reset_index(drop=True)

In [38]:
tdf = pd.DataFrame.from_records(df_growing.uptake.apply(get_elements))
df_growing = pd.merge(df_growing, tdf, left_on='uptake', right_on='reaction')

In [39]:
df_growing

uptake  objective_value     reaction               metabolite  \
0     EX_cytd_e        29.728192    EX_cytd_e                 Cytidine   
1      EX_gsn_e        27.314752     EX_gsn_e                Guanosine   
2      EX_uri_e        25.055581     EX_uri_e                  Uridine   
3      EX_adn_e        20.317783     EX_adn_e                Adenosine   
4      EX_ins_e        20.132444     EX_ins_e                  Inosine   
..          ...              ...          ...                      ...   
57     EX_csn_e         8.318275     EX_csn_e                 Cytosine   
58     EX_ura_e         8.318275     EX_ura_e                   Uracil   
59     EX_xan_e         8.017724     EX_xan_e                 Xanthine   
60   EX_alltn_e         7.093093   EX_alltn_e                Allantoin   
61  EX_2ameph_e         4.772251  EX_2ameph_e  2-Aminoethylphosphonate   

         mid     N     C  
0     cytd_e  True  True  
1      gsn_e  True  True  
2      uri_e  True  True  
3      adn_e  True  True  
4      ins_e  True  True  
..       ...   ...   ...  
57     csn_e  True  True  
58     ura_e  True  True  
59     xan_e  True  True  
60   alltn_e  True  True  
61  2ameph_e  True  True  

[62 rows x 7 columns]

In [40]:
# check that the media is correct

In [41]:
# try to add each pair of exchanges
results = list()
not_open_boundary_ids = [i for i in exchange_ids if (i not in pro99_exchanges) and (i not in df_growing.reaction.values)]

def _check_medium(met1, met2=None):
    with model:
        medium = model.medium
        for m in medium:
            medium[m] = 0.0
        for m in pro99_exchanges:
            medium[m] = 1000.0
        medium["EX_nh4_e"] = 0.0
        medium[met1] = 1000.0
        if met2 is not None:
            medium[met2] = 1000.0
        model.medium = medium
        solution = model.slim_optimize()
        return {'uptake' : met1, 'uptake2' : met2, 'objective_value' : solution}
results = [_check_medium(met1, met2) for met1, met2 in itertools.combinations(not_open_boundary_ids, 2)]        

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

...

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the mos

In [42]:
df = pd.DataFrame(results)

In [43]:
df.head()

uptake          uptake2  objective_value
0  EX_12ppd__R_e    EX_12ppd__S_e     1.592187e-13
1  EX_12ppd__R_e    EX_14glucan_e    -1.921836e-13
2  EX_12ppd__R_e       EX_15dap_e    -5.254737e-13
3  EX_12ppd__R_e    EX_25dkglcn_e     3.347678e-13
4  EX_12ppd__R_e  EX_2m35mdntha_e    -1.733656e-13

In [44]:
df_growing2 = df.loc[(df.objective_value > 1e-5), 
                    ['uptake','uptake2', 'objective_value']
                   ].nlargest(n=1000, columns='objective_value').reset_index(drop=True)

In [45]:
df_growing2

uptake    uptake2  objective_value
0    EX_14glucan_e   EX_nh4_e        30.429427
1    EX_14glucan_e  EX_urea_e        29.906104
2    EX_14glucan_e   EX_no2_e        29.276563
3        EX_lcts_e   EX_nh4_e        29.092801
4         EX_nh4_e   EX_tre_e        28.726116
..             ...        ...              ...
346        EX_co_e   EX_nh4_e         1.689987
347        EX_co_e   EX_no2_e         1.484364
348        EX_co_e   EX_no3_e         1.404266
349        EX_co_e   EX_tnt_e         1.293804
350       EX_h2s_e  EX_urea_e         0.523577

[351 rows x 3 columns]

In [46]:
len(set(df_growing2.uptake.unique()) | set(df_growing2.uptake2.unique()))

76

In [47]:
(set(df_growing2.uptake.unique()) | set(df_growing2.uptake2.unique())) & set(df_growing.uptake.unique())

set()

In [48]:
df_growing2[['reaction', 'metabolite','mid','N','C']] = df_growing2.uptake.apply(get_elements)
df_growing2[['reaction2', 'metabolite2','mid2','N2','C2']] = df_growing2.uptake2.apply(get_elements)

#df_growing = pd.merge(df_growing, tdf, left_on='uptake', right_on='reaction')

In [49]:
df_growing2

uptake    uptake2  objective_value       reaction  \
0    EX_14glucan_e   EX_nh4_e        30.429427  EX_14glucan_e   
1    EX_14glucan_e  EX_urea_e        29.906104  EX_14glucan_e   
2    EX_14glucan_e   EX_no2_e        29.276563  EX_14glucan_e   
3        EX_lcts_e   EX_nh4_e        29.092801      EX_lcts_e   
4         EX_nh4_e   EX_tre_e        28.726116       EX_nh4_e   
..             ...        ...              ...            ...   
346        EX_co_e   EX_nh4_e         1.689987        EX_co_e   
347        EX_co_e   EX_no2_e         1.484364        EX_co_e   
348        EX_co_e   EX_no3_e         1.404266        EX_co_e   
349        EX_co_e   EX_tnt_e         1.293804        EX_co_e   
350       EX_h2s_e  EX_urea_e         0.523577       EX_h2s_e   

             metabolite         mid      N      C  reaction2  \
0    1,4-alpha-D-glucan  14glucan_e  False   True   EX_nh4_e   
1    1,4-alpha-D-glucan  14glucan_e  False   True  EX_urea_e   
2    1,4-alpha-D-glucan  14glucan_e  False   True   EX_no2_e   
3     Lactose C12H22O11      lcts_e  False   True   EX_nh4_e   
4              Ammonium       nh4_e   True  False   EX_tre_e   
..                  ...         ...    ...    ...        ...   
346     Carbon monoxide        co_e  False   True   EX_nh4_e   
347     Carbon monoxide        co_e  False   True   EX_no2_e   
348     Carbon monoxide        co_e  False   True   EX_no3_e   
349     Carbon monoxide        co_e  False   True   EX_tnt_e   
350    Hydrogen sulfide       h2s_e  False  False  EX_urea_e   

               metabolite2    mid2     N2     C2  
0                 Ammonium   nh4_e   True  False  
1              Urea CH4N2O  urea_e   True   True  
2                  Nitrite   no2_e   True  False  
3                 Ammonium   nh4_e   True  False  
4                Trehalose   tre_e  False   True  
..                     ...     ...    ...    ...  
346               Ammonium   nh4_e   True  False  
347                Nitrite   no2_e   True  False  
348                Nitrate   no3_e   True  False  
349  2 4 6 Trinitrotoluene   tnt_e   True  False  
350            Urea CH4N2O  urea_e   True   True  

[351 rows x 13 columns]

### N sources that HOT1A3 can grow on 

In [50]:
df_growing

uptake  objective_value     reaction               metabolite  \
0     EX_cytd_e        29.728192    EX_cytd_e                 Cytidine   
1      EX_gsn_e        27.314752     EX_gsn_e                Guanosine   
2      EX_uri_e        25.055581     EX_uri_e                  Uridine   
3      EX_adn_e        20.317783     EX_adn_e                Adenosine   
4      EX_ins_e        20.132444     EX_ins_e                  Inosine   
..          ...              ...          ...                      ...   
57     EX_csn_e         8.318275     EX_csn_e                 Cytosine   
58     EX_ura_e         8.318275     EX_ura_e                   Uracil   
59     EX_xan_e         8.017724     EX_xan_e                 Xanthine   
60   EX_alltn_e         7.093093   EX_alltn_e                Allantoin   
61  EX_2ameph_e         4.772251  EX_2ameph_e  2-Aminoethylphosphonate   

         mid     N     C  
0     cytd_e  True  True  
1      gsn_e  True  True  
2      uri_e  True  True  
3      adn_e  True  True  
4      ins_e  True  True  
..       ...   ...   ...  
57     csn_e  True  True  
58     ura_e  True  True  
59     xan_e  True  True  
60   alltn_e  True  True  
61  2ameph_e  True  True  

[62 rows x 7 columns]

### when all other potential mediums are available, HOT1A3 can grow on a combination of metabolites

- there is a list of 77 metabolites that enable growth when added to pro99. there are additional 174 metabolites that when all are available, it grows. for now do not pursue this list

In [51]:
# open all additional mediums (all those that do not facilitate growth by themselves)
not_open_boundary_ids = [i for i in exchange_ids if (i not in pro99_exchanges) and 
                         (i not in df_growing.reaction.values) and
                         (i not in df_growing2.reaction.values) and
                         (i not in df_growing2.reaction2.values)
                        ]
with model:
    medium = model.medium
    for m in medium:
        medium[m] = 0.0
    for m in pro99_exchanges:
        medium[m] = 1000.0
    medium["EX_nh4_e"] = 0.0
    for i in not_open_boundary_ids:
        medium[i] = 1000.0
    model.medium = medium
    solution = model.optimize()
    print(model.summary())


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


Objective
1.0 Growth = 0.0

Uptake
------
Empty DataFrame
Columns: [Metabolite, Reaction, Flux, C-Number, C-Flux]
Index: []

Secretion
---------
Empty DataFrame
Columns: [Metabolite, Reaction, Flux, C-Number, C-Flux]
Index: []



In [52]:
len(not_open_boundary_ids), len(exchange_ids), len(pro99_exchanges), len(df_growing.reaction)

(100, 238, 19, 62)

In [53]:
len(set(df_growing2.reaction) |set(df_growing2.reaction2))

76

In [54]:
251-19-77

155

### Force HOT1A3 to uptake the potential N/C sources, limit growth (biomass), and see what is secreted

In [55]:
def _force_feeding(met1):
    with model:
        medium = model.medium
        for m in medium:
            medium[m] = 0.0
        for m in pro99_exchanges:
            medium[m] = 1000.0
        medium["EX_nh4_e"] = 0.0
        medium[met1] = 1000.0
        model.medium = medium
        model.reactions.get_by_id(met1).upper_bound = -1e-5
        model.reactions.Growth.upper_bound = 1e-2
        solution = model.slim_optimize()
        #print(met1, model.summary())
        print(met1)
        fluxes = flux_variability_analysis(model, model.boundary, loopless=True, fraction_of_optimum=0.9, processes=11)
        fluxes['uptake'] = met1
        return fluxes
fluxes_df_list = [_force_feeding(met1) for met1 in df_growing['uptake']]

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_cytd_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_gsn_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


...

EX_xan_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_alltn_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_2ameph_e


In [ ]:
def _force_feeding2(met1, met2):
    with model:
        medium = model.medium
        for m in medium:
            medium[m] = 0.0
        for m in pro99_exchanges:
            medium[m] = 1000.0
        medium["EX_nh4_e"] = 0.0
        medium[met1] = 1000.0
        medium[met2] = 1000.0
        model.medium = medium
        model.reactions.get_by_id(met1).upper_bound = -1e-5
        model.reactions.get_by_id(met2).upper_bound = -1e-5
        model.reactions.Growth.upper_bound = 1e-2
        solution = model.slim_optimize()
        #print(met1, model.summary())
        print(met1, met2)
        fluxes = flux_variability_analysis(model, model.boundary, loopless=True, fraction_of_optimum=0.9, processes=11)
        fluxes['uptake'] = met1
        fluxes['uptake2'] = met2
        return fluxes
fluxes2_df_list = [_force_feeding2(met1, met2) for met1, met2 in zip(df_growing2['uptake'], df_growing2['uptake2'])]

Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_14glucan_e EX_nh4_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_14glucan_e EX_urea_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


...

EX_no3_e EX_phenona_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_no3_e EX_phedca_e


Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.
Could not identify an external compartment by name and choosing one with the most boundary reactions. That might be complete nonsense or change suddenly. Consider renaming your compartments using `Model.compartments` to fix this.


EX_pheocta_e EX_urea_e


In [ ]:
force_feeding_df = pd.concat(fluxes_df_list)

In [ ]:
force_feeding2_df = pd.concat(fluxes2_df_list)

In [ ]:
force_feeding_df.index = force_feeding_df.index.set_names(['secretion'])
force_feeding_df = force_feeding_df.reset_index()
force_feeding_df.head()

In [ ]:
force_feeding2_df.index = force_feeding2_df.index.set_names(['secretion'])
force_feeding2_df = force_feeding2_df.reset_index()
force_feeding2_df.head()

In [ ]:
force_feeding_df.loc[force_feeding_df.maximum > 1e-3].groupby('secretion').minimum.count()

In [ ]:
force_feeding2_df.loc[force_feeding2_df.maximum > 1e-3].groupby('secretion').minimum.count()

In [ ]:
drop_columns = ['EX_co2_e',  'EX_fe3_e','EX_h2o_e',
       'EX_h_e', 'EX_o2_e',]

n_exchange_df = force_feeding_df.loc[(force_feeding_df.maximum > 1e-3) & (~force_feeding_df.secretion.isin(drop_columns))]
pdf = n_exchange_df.pivot_table(columns='uptake', index='secretion', values='maximum', fill_value=0)


In [ ]:
drop_columns = ['EX_co2_e',  'EX_fe3_e','EX_h2o_e',
       'EX_h_e', 'EX_o2_e',]

n_exchange2_df = force_feeding2_df.loc[(force_feeding2_df.maximum > 1e-3) & (~force_feeding2_df.secretion.isin(drop_columns))]
#pdf2 = n_exchange2_df.pivot_table(columns='uptake', index='secretion', values='maximum', fill_value=0)


In [ ]:
tdf = n_exchange_df.uptake.apply(get_elements)
n_exchange_df[['metabolite_uptake', 'mid_uptake', 'N_uptake', 'C_uptake']] = tdf[['metabolite', 'mid', 'N', 'C']]

tdf = n_exchange_df.secretion.apply(get_elements)
n_exchange_df[['metabolite_secretion', 'mid_secretion', 'N_secretion', 'C_secretion']] = tdf[['metabolite','mid', 'N', 'C']]

n_exchange_df.head()

In [ ]:
tdf = n_exchange2_df.uptake.apply(get_elements)
n_exchange2_df[['metabolite_uptake', 'mid_uptake', 'N_uptake', 'C_uptake']] = tdf[['metabolite', 'mid','N', 'C']]

tdf = n_exchange2_df.uptake2.apply(get_elements)
n_exchange2_df[['metabolite_uptake2', 'mid_uptake2', 'N_uptake2', 'C_uptake2']] = tdf[['metabolite', 'mid','N', 'C']]

tdf = n_exchange2_df.secretion.apply(get_elements)
n_exchange2_df[['metabolite_secretion', 'mid_secretion','N_secretion', 'C_secretion']] = tdf[['metabolite','mid', 'N', 'C']]

n_exchange2_df.head()

In [ ]:
col_anno = pd.DataFrame.from_records([get_elements(i) for i in pdf.columns])
row_anno = pd.DataFrame.from_records([get_elements(i) for i in pdf.index])
N_lut = {True: '#BF9270', False : '#FFEDDB'}
C_lut = {True: '#94B49F', False : '#FCF8E8'}
row_anno.N = row_anno.N.map(N_lut)
row_anno.C = row_anno.C.map(C_lut)
col_anno.N = col_anno.N.map(N_lut)
col_anno.C = col_anno.C.map(C_lut)
row_anno.index = row_anno.reaction
col_anno.index = col_anno.reaction

In [ ]:

sns.clustermap(pdf, norm=LogNorm(), 
               cmap='coolwarm', figsize=(25,15), 
               linewidths=0.1, #cbar_kws= dict(location='right'),
               row_colors=row_anno[['N', 'C']],
               col_colors=col_anno[['N', 'C']],
               yticklabels= row_anno.metabolite,
               xticklabels= col_anno.metabolite,
               colors_ratio=0.04,
              robust=True, cbar_pos=(1, .2, .03, .4),
              dendrogram_ratio=0.02)
plt.suptitle("Maximum FVA Flux - secretion when 'force fed'", y=1)

In [ ]:
pdf.shape

In [ ]:
len(exchange_ids)

In [ ]:
# Create a Pandas Excel writer using XlsxWriter as the engine.
writer = pd.ExcelWriter('ALT_N_sources.xlsx', engine='xlsxwriter')

# Write each dataframe to a different worksheet.
df_growing.to_excel(writer, sheet_name='uptake')
df_growing2.to_excel(writer, sheet_name='uptake2')
n_exchange_df.to_excel(writer, sheet_name='secretion')
n_exchange2_df.to_excel(writer, sheet_name='secretion2')

# Close the Pandas Excel writer and output the Excel file.
writer.save()

In [ ]:
n_exchange_df.shape,n_exchange2_df.shape

In [ ]:
n_exchange_df.head(50)

In [ ]:
model.genes[30]